In [27]:
#import "lidar_calibration_data.csv"
import csv
import numpy as np
import json

#data is in {'f': [359, 359, 351, 341, 340, 332, 331, 327, 323, 321, 319, 321, 309, 307, 300, 293, 296, 297, 296, 292, 286, 283, 280, 283, 278, 275, 273, 274, 270, 271, 270, 271, 264, 264, 261, 263, 259, 262, 261, 255, 260, 256, 256, 258, 254, 255, 256, 255, 255, 255, 257, 252, 256, 257, 251, 260, 258, 261, 255, 261, 257, 264, 261, 259, 259, 260, 267, 261, 267, 268, 270, 273, 275, 269, 278, 277, 277, 283, 284, 290, 285, 287, 293, 295, 296, 303, 304, 300, 300, 314, 308, 311, 316, 316, 320, 328, 328, 336, 334, 341, 331]}, 27.5
#dictionary, float

#read as text file and store in a variable
data = open('lidar_calibration_data.csv', 'r')
data = data.read()

#split the data into lines
data = data.split('\n')

#slpit by , and seperate only the last item
measured = np.array([float((i.split(',')[-1]).strip()) for i in data if i != ''])
#remove the last item and join the rest of the items
distance = np.array([json.loads((','.join(i.split(',')[:-1])).replace("'", '"'))['f'] for i in data if i != ''])

In [28]:
def make_dataset(measured, distance, front_start = 40, front_end = 140, num_readings = 101, fix_offset = 35):
    
    #json data 'f': [a, b, c, d, e, f, g...................]
    #offset is till the root of the servo
    x = distance
    angles = np.linspace(np.deg2rad(front_start), np.deg2rad(front_end), num_readings)

    # x sin(angles) = measured
    y = (measured / np.sin(angles))*10 - fix_offset

    #if x is 0, y is 0
    y[x == 0] = 0

    return x,y

#loop through the data and print the x and y values
x = []
y = []
for i in range(len(measured)):
    x_, y_ = make_dataset(measured[i], distance[i])
    x.append(x_)
    y.append(y_)

x, y = np.array(x), np.array(y)
x,y

(array([[401,   0, 452, ...,   0,   0,   0],
        [498, 463, 525, ...,   0,   0,   0],
        [  0, 519,   0, ..., 713,   0, 780],
        ...,
        [ 99,  98,  95, ..., 155, 158, 156],
        [ 97,  97, 102, ..., 146, 151, 155],
        [ 97,  97,  93, ..., 153, 157, 158]]),
 array([[652.62993147,   0.        , 625.55863504, ...,   0.        ,
           0.        ,   0.        ],
        [652.62993147, 638.71986432, 625.55863504, ...,   0.        ,
           0.        ,   0.        ],
        [  0.        , 638.71986432,   0.        , ..., 625.55863504,
           0.        , 652.62993147],
        ...,
        [126.79527799, 123.52232102, 120.42556119, ..., 120.42556119,
         123.52232102, 126.79527799],
        [126.79527799, 123.52232102, 120.42556119, ..., 120.42556119,
         123.52232102, 126.79527799],
        [126.79527799, 123.52232102, 120.42556119, ..., 120.42556119,
         123.52232102, 126.79527799]]))

In [29]:
#import pytorch
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F

#set cuda device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

def get_batch(n):
    #randomly select n samples from the dataset
    indices = np.random.randint(0, len(x), n)
    #return as pytorch tensor
    return torch.tensor(x[indices], dtype=torch.float32).to(device), torch.tensor(y[indices], dtype=torch.float32).to(device)

get_batch(2)

(tensor([[218., 214., 210., 207., 208., 205., 201., 194., 196., 194., 193., 193.,
          194., 189., 183., 188., 185., 181., 179., 179., 178., 178., 175., 175.,
          174., 170., 175., 171., 171., 170., 166., 167., 170., 164., 168., 164.,
          167., 165., 164., 167., 164., 167., 163., 167., 166., 164., 165., 167.,
          169., 167., 168., 171., 172., 171., 175., 172., 171., 174., 176., 174.,
          178., 177., 180., 180., 179., 185., 185., 187., 188., 192., 191., 195.,
          193., 192., 201., 205., 206., 202., 203., 211., 218., 221., 224., 229.,
          229., 227., 243., 245., 248., 249., 254., 255., 263., 269., 283., 284.,
          302., 306., 323., 321., 324.],
         [531., 533., 517., 491., 495., 491., 490., 482., 473., 461., 465., 466.,
          454., 458., 447., 445., 444., 438., 439., 435., 424., 436., 424., 417.,
          425., 420., 417., 411., 416., 414., 411., 411., 409., 406., 412., 403.,
          406., 409., 406., 403., 410., 411., 412., 408.,

In [30]:
import torch
import torch.nn as nn
import torch.nn.functional as F

class Linear(nn.Module):
    
    def __init__(self, input_dim):
        super(Linear, self).__init__()
        # Each element has its own weight for multiplication
        self.weights = nn.Parameter(torch.randn(input_dim))
        # Each element has its own bias for addition
        self.biases = nn.Parameter(torch.randn(input_dim))

    def forward(self, x):
        # Element-wise multiplication and addition
        return x * self.weights + self.biases

class Model(nn.Module):

    def __init__(self):
        
        super(Model, self).__init__()
        # Linear layer
        self.l1a = Linear(101)
        self.l1b = Linear(101)
        self.l1c = Linear(101)

        self.l6 = Linear(101)
        self.l7 = Linear(101)
        self.l8 = Linear(101)
        self.l9 = Linear(101)
        self.l10 = Linear(101)
        self.l11 = Linear(101)
        self.l12 = Linear(101)
        self.l13 = Linear(101)
        
        # Create a constant array (e.g., cosine values from 40 to 140 degrees)
        degrees = np.arange(40, 141)  # Create an array from 40 to 140
        radians = np.deg2rad(degrees)  # Convert degrees to radians
        cosine_values = np.cos(radians)  # Compute cosine
        
        # Convert the numpy array to a torch tensor and then to a Parameter, setting requires_grad to False
        self.cosine_constant = nn.Parameter(torch.tensor(cosine_values, dtype=torch.float32), requires_grad=False)

    def forward(self, x):

        #Each index is dependent on the previous and the next index 
        x_left_shift = torch.roll(x, 1, 1) 
        x_left_shift[:, -1] = 0

        x_right_shift = torch.roll(x, -1, 1)
        x_right_shift[:, 0] = 0

        x_pure_a = self.l1a(x)
        x_pure_b = self.l1b(x)

        x_front = self.l6(x_left_shift) + self.l7(x_right_shift) + x_pure_b
        x_front = F.gelu(self.l8(x_front))
        x_front = F.gelu(self.l9(x_front))
        x_front = self.l10(x_front)
        x_front = F.gelu(self.l11(x_front))
        x_front = self.l12(x_front)

        x_pure_c = self.l1c(x)
        x_angles = self.l13(self.cosine_constant*x_pure_c)

        return x + x_front + x_pure_a + x_angles

model = Model().to(device)

In [33]:
#loss function
criterion = nn.MSELoss()

#optimizer
optimizer = optim.Adam(model.parameters(), lr=0.00001)

#training loop
n_epochs = 100000
batch_size = 70

for epoch in range(n_epochs):
    
    x_batch, y_batch = get_batch(batch_size)

    #forward pass
    output = model(x_batch)
    loss = criterion(output, y_batch)

    #backward pass
    optimizer.zero_grad()
    loss.backward()

    #update weights
    optimizer.step()

    print(f'Epoch: {epoch}, Loss: {loss.item()}')

#save the model
torch.save(model.state_dict(), 'calibration_model.pth')

#test the model
x_test, y_test = get_batch(1)
y_pred = model(x_test)

y_test, y_pred

Epoch: 0, Loss: 166.44871520996094
Epoch: 1, Loss: 166.55809020996094
Epoch: 2, Loss: 118.22052001953125
Epoch: 3, Loss: 165.1576385498047
Epoch: 4, Loss: 177.42234802246094
Epoch: 5, Loss: 171.06875610351562
Epoch: 6, Loss: 152.31236267089844
Epoch: 7, Loss: 206.57421875
Epoch: 8, Loss: 165.1080322265625
Epoch: 9, Loss: 137.77813720703125
Epoch: 10, Loss: 133.69796752929688
Epoch: 11, Loss: 123.82195281982422
Epoch: 12, Loss: 181.89585876464844
Epoch: 13, Loss: 133.25650024414062
Epoch: 14, Loss: 169.3977508544922
Epoch: 15, Loss: 116.61333465576172
Epoch: 16, Loss: 169.85391235351562
Epoch: 17, Loss: 105.7907485961914
Epoch: 18, Loss: 161.8055419921875
Epoch: 19, Loss: 159.73207092285156
Epoch: 20, Loss: 126.92464447021484
Epoch: 21, Loss: 136.38063049316406
Epoch: 22, Loss: 163.67340087890625
Epoch: 23, Loss: 115.8397216796875
Epoch: 24, Loss: 171.07859802246094
Epoch: 25, Loss: 159.57310485839844
Epoch: 26, Loss: 134.05056762695312
Epoch: 27, Loss: 175.69956970214844
Epoch: 28, Los

(tensor([[  0.0000,   0.0000, 625.5587,   0.0000,   0.0000,   0.0000,   0.0000,
            0.0000, 559.7697, 550.6558, 541.9901, 533.7477,   0.0000,   0.0000,
          511.3420, 504.5824, 498.1483,   0.0000,   0.0000, 480.6519, 475.3776,
          470.3625, 465.5959, 461.0682, 456.7701,   0.0000, 448.8292, 445.1713,
          441.7123, 438.4461, 435.3666, 432.4684, 429.7463, 427.1958, 424.8123,
          422.5921, 420.5312, 418.6264, 416.8745, 415.2728, 413.8186, 412.5096,
          411.3438, 410.3193, 409.4347, 408.6884, 408.0793, 407.6066, 407.2694,
          407.0673, 407.0000, 407.0673, 407.2694, 407.6066, 408.0793, 408.6884,
          409.4347, 410.3193, 411.3438, 412.5096, 413.8186, 415.2728, 416.8745,
          418.6264, 420.5312, 422.5921, 424.8123, 427.1958,   0.0000, 432.4684,
          435.3666, 438.4461, 441.7123,   0.0000, 448.8292, 452.6931,   0.0000,
          461.0682,   0.0000, 470.3625, 475.3776,   0.0000,   0.0000,   0.0000,
            0.0000, 504.5824,   0.0000, 

In [35]:
#load the model
model = Model().to(device)
model.load_state_dict(torch.load('calibration_model.pth'))

#test the model
x_test, y_test = get_batch(1)
y_pred = model(x_test)

#calculate loss
y_pred, y_test

(tensor([[388.5106, 379.5392, 375.2609, 372.9041, 377.2823, 354.8411, 356.2775,
          344.7574, 336.8184, 331.7466, 327.1269, 317.4290, 317.3297, 311.5645,
          308.4364, 305.7501, 294.9163, 294.0591, 290.6673, 284.0496, 276.6073,
          278.1186, 277.7325, 268.1720, 271.8908, 269.8759, 260.8038, 263.8378,
          256.8257, 260.2852, 253.5613, 257.5743, 255.5399, 255.8703, 250.8735,
          249.1509, 246.9039, 243.1066, 245.3950, 244.9052, 247.6519, 246.3259,
          243.5001, 242.6208, 244.5157, 237.0481, 241.4631, 242.6975, 236.6277,
          239.8976, 237.5301, 235.9665, 237.5497, 235.2487, 237.2644, 240.1176,
          235.1683, 241.1054, 236.8897, 246.6320, 238.7677, 246.1238, 245.3004,
          246.5405, 249.6471, 249.2072, 251.6587, 255.3433, 250.5984, 259.2620,
          250.8780, 261.0057, 264.8102, 259.0470, 262.5086, 264.3172, 272.1086,
          268.8976, 274.0683, 273.8751, 279.5626, 279.9166, 283.5043, 289.1690,
          298.3353, 294.4765, 304.6460, 

In [105]:
#load Head
model2 = Model().to(device)
model2.load_state_dict(torch.load('calibration_model.pth.bak'))

#test the model
x_test, y_test = get_batch(1)
y_pred = model2(x_test)

#calculate loss
criterion(y_pred, y_test)

tensor(115.7477, device='cuda:0', grad_fn=<MseLossBackward0>)